In [175]:
# Useful for defining quantities
from astropy import units as u
from astropy.coordinates import cartesian_to_spherical

# Earth focused modules, ISS example orbit and time span generator
from poliastro.earth import EarthSatellite
from poliastro.earth.plotting import GroundtrackPlotter
from poliastro.twobody import Orbit
from poliastro.spacecraft import Spacecraft
from poliastro.examples import iss
from poliastro.util import time_range
from poliastro.bodies import Earth

In [130]:
import numpy as np
import matplotlib.pyplot as plt
from scipy import interpolate

In [2]:
from ipywidgets import interact, interactive, fixed, interact_manual, FloatSlider, IntSlider
import ipywidgets as widgets

In [25]:
radius_E = 6400

In [107]:
store = lambda: None

In [242]:
@interact(h=FloatSlider(min=7000, max=19000,value=11500, step=100, continuous_update=False),
          i=FloatSlider(min=0, max=90, step=1, continuous_update=False),
          duration=IntSlider(min=20, max=300, step=10, continuous_update=False),
          max_day_bn_rep=IntSlider(value=2,min=1, max=30, step=1, continuous_update=False))
def groundtract(h, i, duration,max_day_bn_rep):
    # Build spacecraft instance
    a = (radius_E+h) * u.km
    ecc = 0 * u.one
    inc = i * u.deg
    raan = 0 * u.deg
    argp = 0 * u.deg
    nu = 0 * u.deg
    orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)
    print("Original period: ", orb.period.to(u.h))
    #adjust to integer orbits in a day
    T_E =  Earth.rotational_period.to(u.s)
    ratio =T_E/orb.period 
    ratio = np.floor(max_day_bn_rep*ratio)/float(max_day_bn_rep)*u.one
    new_period = T_E/ratio
    a = (Earth.k*(new_period/2/np.pi)**2)**(1./3)
    orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)

    print("Adjusted period: ", orb.period.to(u.h), "Adjusted altitude: ", (a - radius_E*u.km).to(u.km))
    sat = EarthSatellite(orb, None)
    t_span = time_range(orb.epoch, periods=5*duration, end= orb.epoch + duration*u.h)
    gp = GroundtrackPlotter()
    gp.update_layout(title="Groundtrack")

    # Plot previously defined EarthSatellite object
    gp.plot(
        sat,
        t_span,
        label="Sat",
        color = "red",
    )
    store.gp_groundtract = gp
    store.sat = sat
    store.t_span = t_span
    store.t_end = duration*u.h
    gp.fig.show()

interactive(children=(FloatSlider(value=11500.0, continuous_update=False, description='h', max=19000.0, min=70…

In [112]:
store.gp_groundtract.update_geos(projection_type="orthographic")


In [244]:
@interact(ground_size=FloatSlider(min=0,max=30,value=10,continuous_update=False),
          n_sats = IntSlider(min=6,max=3600,value=18, continuous_update=False))
def groundshadow(ground_size, n_sats):
    # ground_size in degrees is the size of a tile on the surface
    # n_sats is the number of satelites on one repetion of an orbit
    # for heights > continuous coverage height, n_sats * grounds_size can be = 350
    # below continous coverage height, more n_sats are needed
    data = store.gp_groundtract.fig.data[1]
    ts = store.t_span-store.sat.orbit.epoch
    lats = interpolate.interp1d(ts.to(u.h), data['lat'])
    lons = interpolate.interp1d(ts.to(u.h), data['lon'])
    theta = np.linspace(2*np.pi,0)
    dt = store.sat.orbit.period.to(u.h)/n_sats
    t0 = ts[0].to(u.h)
    tend = ts[-1].to(u.h)
    for t in np.linspace(t0,tend,int(tend/dt)):
        store.gp_groundtract.fig.add_scattergeo(mode='text',fill='toself',fillcolor='blue', 
                      lat=lats(t)+ground_size/2*np.sin(theta),
                      lon=lons(t)+ground_size/2*np.cos(theta),
                                                opacity=0.1)
    store.gp_groundtract.update_geos()
    store.gp_groundtract.fig.show()

interactive(children=(FloatSlider(value=10.0, continuous_update=False, description='ground_size', max=30.0), I…

In [34]:
a = 7000 * u.km
ecc = 0 * u.one
inc = 10 * u.deg
raan = 0 * u.deg
argp = 0 * u.deg
nu = 0 * u.deg
orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)
print("Original period: ", orb.period.to(u.h))
sat = EarthSatellite(orb, None)
t_span = time_range(orb.epoch, periods=505, end=orb.epoch+10 * u.h)
gp = GroundtrackPlotter()
gp.update_layout(title="Groundtrack")

# Plot previously defined EarthSatellite object
gp.plot(
    sat,
    t_span,
    label="Sat",
    color = "red",
    marker={"size": 10, "symbol": "triangle-right", "line": {"width": 1, "color": "black"}},
)

Original period:  1.6190323993572264 h


In [266]:
groundtract(11700, 80, 48,6)
groundshadow(20, 18)

Original period:  6.7317246260881 h
Adjusted period:  6.838421485714274 h Adjusted altitude:  11890.75321705091 km


In [267]:
# Build spacecraft instance
h, i, duration, max_day_bn_rep = 11700, 80, 48, 6
a = (radius_E+h) * u.km
ecc = 0 * u.one
inc = i * u.deg
raan = 0 * u.deg
argp = 60 * u.deg
nu = 0 * u.deg
orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)
print("Original period: ", orb.period.to(u.h))
#adjust to integer orbits in a day
T_E =  Earth.rotational_period.to(u.s)
ratio =T_E/orb.period 
ratio = np.floor(max_day_bn_rep*ratio)/float(max_day_bn_rep)*u.one
new_period = T_E/ratio
a = (Earth.k*(new_period/2/np.pi)**2)**(1./3)
orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)

print("Adjusted period: ", orb.period.to(u.h), "Adjusted altitude: ", (a - radius_E*u.km).to(u.km))
sat = EarthSatellite(orb, None)
t_span = time_range(orb.epoch, periods=5*duration, end= orb.epoch + duration*u.h)
gp = store.gp_groundtract
gp.update_layout(title="Groundtrack")

# Plot previously defined EarthSatellite object
gp.plot(
    sat,
    t_span,
    label="Sat",
    color = "green",
)
store.gp_groundtract = gp
store.sat = sat
store.t_span = t_span
store.t_end = duration*u.h
gp.fig.show()

Original period:  6.7317246260881 h
Adjusted period:  6.838421485714274 h Adjusted altitude:  11890.75321705091 km


In [268]:
store.gp_groundtract.fig.data

(Scattergeo(),
 Scattergeo({
     'lat': array([-1.44275397e-03,  1.04088743e+01,  2.08077544e+01, ..., -1.40270841e+01,
                   -3.61935598e+00,  6.79219350e+00]),
     'line': {'color': 'red'},
     'lon': array([79.80606316, 78.64196658, 77.60746633, ..., 81.35148263, 80.21673522,
                   79.03866413]),
     'mode': 'lines',
     'name': 'Sat'
 }),
 Scattergeo({
     'lat': array([-0.00144275]),
     'lon': array([79.80606316]),
     'marker': {'color': 'red'},
     'name': 'Sat',
     'showlegend': False
 }),
 Scattergeo({
     'fill': 'toself',
     'fillcolor': 'blue',
     'lat': array([-1.44275397e-03, -1.28021437e+00, -2.53798859e+00, -3.75411280e+00,
                   -4.90861827e+00, -5.98254806e+00, -6.95826826e+00, -7.81975758e+00,
                   -8.55287038e+00, -9.14556898e+00, -9.58812128e+00, -9.87326059e+00,
                   -9.99630492e+00, -9.95523388e+00, -9.75072188e+00, -9.38612697e+00,
                   -8.86743582e+00, -8.20316530e

In [269]:
ground_size, n_sats = 20, 18

data = store.gp_groundtract.fig.data[-2]
ts = store.t_span-store.sat.orbit.epoch
lats = interpolate.interp1d(ts.to(u.h), data['lat'])
lons = interpolate.interp1d(ts.to(u.h), data['lon'])
theta = np.linspace(2*np.pi,0)
dt = store.sat.orbit.period.to(u.h)/n_sats
t0 = ts[0].to(u.h)
tend = ts[-1].to(u.h)
for t in np.linspace(t0,tend,int(tend/dt)):
    store.gp_groundtract.fig.add_scattergeo(mode='text',fill='toself',fillcolor='green', 
                  lat=lats(t)+ground_size/2*np.sin(theta),
                  lon=lons(t)+ground_size/2*np.cos(theta),
                                            opacity=0.1)
store.gp_groundtract.update_geos()
store.gp_groundtract.fig.show()

In [274]:
gp.update_geos(projection_type="orthographic")

In [272]:
points1 = store.gp_groundtract.fig.data[1]
points2 = store.gp_groundtract.fig.data[129]

Scattergeo({
    'lat': array([58.5232161 , 68.23688607, 76.67114963, ..., 44.86504152, 55.03942212,
                  64.93478395]),
    'line': {'color': 'red'},
    'lon': array([ 96.5474241 , 103.00072888, 121.86890119, ...,  93.98600699,
                   95.46546249,  99.98766791]),
    'mode': 'lines',
    'name': 'Sat'
})

In [279]:
np.savetxt(f'cache/actually_looks_good_2src.csv',
            np.vstack([
                np.vstack([points1['lat'],points1['lon']]).T, 
                np.vstack([points2['lat'],points2['lon']]).T]),
                delimiter=',')